In [1]:
import os
import sys
import yfinance as yf
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import warnings
from scipy.stats import ttest_1samp


In [2]:
warnings.filterwarnings('ignore')
path = os.getenv("ROOT_PATH")
sys.path.append(path)
print(path)


/Users/monic/Desktop/Master_Thesis/empirical


## Statistical Significance - Table 3b - Mid

The first step is creating a table with the daily ARs calculated using CAPM for each company

In [3]:
window_size = 250
risk_free_rate_df= pd.read_excel(f"{path}/raw_data/main/risk_free.xlsx")
risk_free_rate_df['Swedish Treasury Bills (SE TB 1 Month)'].fillna(method='ffill', inplace=True)
risk_free_rate_df['Swedish Treasury Bills (SE TB 1 Month)']= (1 + risk_free_rate_df['Swedish Treasury Bills (SE TB 1 Month)']) ** (1/250) - 1
df_price_2013 = pd.read_excel(f"{path}/raw_data/main/price_2013.xlsx")

ARs_df = pd.merge(df_price_2013,risk_free_rate_df,left_on='Date',right_on='Date',how='left')
ARs_df['market_returns'] = df_price_2013['^OMXSPI'].pct_change()
ARs_df.drop(columns='^OMXSPI',inplace=True)


In [4]:
ARs_df.head()


Date  8TRA.ST     AAK.ST      ABB.ST    ABLI.ST  ACAD.ST  ACE.ST  \
0 2013-03-06      NaN  42.981308  134.692978  17.437082      NaN     NaN   
1 2013-03-07      NaN  43.194801  134.233261  17.437082      NaN     NaN   
2 2013-03-08      NaN  43.123638  134.141327  17.212570      NaN     NaN   
3 2013-03-11      NaN  42.910152  134.049377  17.137733      NaN     NaN   
4 2013-03-12      NaN  43.692932  133.497757  17.212570      NaN     NaN   

   ACRI-A.ST  ACRI-B.ST    ACTI.ST  ...  WBGR-B.ST    WIHL.ST    WISE.ST  \
0        NaN        NaN  30.363342  ...        NaN  19.381405  20.741724   
1        NaN        NaN  33.174763  ...        NaN  19.560863  21.486933   
2        NaN        NaN  34.861614  ...        NaN  19.471134  20.990126   
3        NaN        NaN  35.705040  ...        NaN  19.471134  21.362732   
4        NaN        NaN  35.002186  ...        NaN  19.201946  20.865921   

   WTW-A.ST  XANO-B.ST  XBRANE.ST  XSPRAY.ST  XVIVO.ST  \
0       NaN   6.276816        NaN        NaN      20.4   
1       NaN   6.147664        NaN        NaN      20.5   
2       NaN   6.199325        NaN        NaN      20.6   
3       NaN   6.302645        NaN        NaN      20.6   
4       NaN   6.354307        NaN        NaN      20.6   

   Swedish Treasury Bills (SE TB 1 Month)  market_returns  
0                                   1.030             NaN  
1                                   1.050        0.099423  
2                                   0.970        1.377876  
3                                   1.050        0.467752  
4                                   1.035       -1.992477  

[5 rows x 396 columns]

In [5]:
for column in df_price_2013.columns[1:-1]:  # Exclude the 'Date' and '^OMXSPI' column

    stock_returns = ARs_df[column].pct_change()

    result_df = pd.DataFrame({
    'Date': ARs_df['Date'],
    'Stock_Returns': stock_returns,
    'Market_Returns': ARs_df['market_returns']})

    result_df['beta'] = result_df['Stock_Returns'].rolling(window=window_size).cov(result_df['Market_Returns']).div(result_df['Market_Returns'].rolling(window=window_size).var())
    result_df = pd.merge(result_df,ARs_df[['Date','Swedish Treasury Bills (SE TB 1 Month)']], left_on='Date',right_on='Date', how='left')

    # Ri = Rf + beta * (Rm-Rf) + ei --> Ri - [Rf + beta * (Rm - Rf)]
    result_df['MMAR'] = result_df['Swedish Treasury Bills (SE TB 1 Month)']+ result_df['beta'] * (result_df['Market_Returns'] - result_df['Swedish Treasury Bills (SE TB 1 Month)'])

    ARs_df[f'{column}_ARs'] = result_df['Stock_Returns'] - result_df['MMAR']
    ARs_df.drop(columns=f'{column}',inplace=True)


### **Proxy B :**

Daily raw stock returns with absolute values exceeding 3 and 4 standard deviations by market returns sign and market capitalization.

In [6]:
proxy_b_df = pd.read_excel(f'{path}/raw_data/main/proxy_b.xlsx')
df_mid = pd.read_excel (f'{path}/raw_data/main/mid_caps.xlsx')
total_b_df = pd.merge(proxy_b_df,ARs_df,on='Date',how='left')


In [7]:
total_b_df.head()


Date  8TRA.ST_Increase_3std  8TRA.ST_Decrease_3std  \
0 2014-03-06                      0                      0   
1 2014-03-07                      0                      0   
2 2014-03-10                      0                      0   
3 2014-03-11                      0                      0   
4 2014-03-12                      0                      0   

   8TRA.ST_Increase_4std  8TRA.ST_Decrease_4std  AAK.ST_Increase_3std  \
0                      0                      0                     0   
1                      0                      0                     0   
2                      0                      0                     0   
3                      0                      0                     0   
4                      0                      0                     0   

   AAK.ST_Decrease_3std  AAK.ST_Increase_4std  AAK.ST_Decrease_4std  \
0                     0                     0                     0   
1                     0                     0                     0   
2                     0                     0                     0   
3                     0                     0                     0   
4                     0                     0                     0   

   ABB.ST_Increase_3std  ...  VPLAY-B.ST_ARs  WALL-B.ST_ARs  WBGR-B.ST_ARs  \
0                     0  ...             NaN            NaN            NaN   
1                     0  ...             NaN       0.284278            NaN   
2                     0  ...             NaN       0.551437            NaN   
3                     0  ...             NaN       2.285070            NaN   
4                     0  ...             NaN      -2.563473            NaN   

   WIHL.ST_ARs  WISE.ST_ARs  WTW-A.ST_ARs  XANO-B.ST_ARs  XBRANE.ST_ARs  \
0          NaN          NaN           NaN            NaN            NaN   
1     1.712153     2.648586           NaN       0.123482            NaN   
2    -1.087446     1.543361           NaN      -2.931026            NaN   
3    -1.003612     5.536781           NaN      -0.285982            NaN   
4    -1.095838    -1.455698           NaN       6.127125            NaN   

   XSPRAY.ST_ARs  XVIVO.ST_ARs  
0            NaN           NaN  
1            NaN    -10.518450  
2            NaN     -4.078193  
3            NaN      3.144449  
4            NaN     10.897615  

[5 rows x 3726 columns]

#### Price increases with market increases: 

##### Testing events individually: 

In [8]:

# Create a dictionary to store the result for each threshold
results_dict_b_three_increase_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

results_dict_b_four_increase_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_3std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue


        results_dict_b_three_increase_m['Company'].append(i)
        results_dict_b_three_increase_m['Event_Date'].append(event_date)
        results_dict_b_three_increase_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_increase_m['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_three_increase_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_increase_m['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_three_increase_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_increase_m['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_three_increase_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_three_increase_m['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_three_increase_m = pd.DataFrame(results_dict_b_three_increase_m)


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_4std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue

        results_dict_b_four_increase_m['Company'].append(i)
        results_dict_b_four_increase_m['Event_Date'].append(event_date)
        results_dict_b_four_increase_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_increase_m['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_four_increase_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_increase_m['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_four_increase_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_increase_m['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_four_increase_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_four_increase_m['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_four_increase_m = pd.DataFrame(results_dict_b_four_increase_m)
print(results_significance_b_three_increase_m.head())
print(results_significance_b_four_increase_m.head())


Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next Day Returns: 0.25061959646604615 , P value: nan 
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 2 Days Returns: -1.97577369993215,P value: 0.5379234383337155 
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 5 Days Returns: 0.7669898161524522,P value: 0.689432869082613 
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 20 Days Returns: 0.2875533134243679,P value: 0.6082926321036635 
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next Day Returns: -4.986209008332078 , P value: nan 
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 2 Days Returns: -3.3488321812843873,P value: 0.28950936122540355 
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 5 Days Returns: -1.7053771556136645,P value: 0.4282928111318337 
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 20 Days Returns: -0.012487821302648517,P value: 0.9877683299479488 
Company: ACAD.ST, Date: 2019-01-16 00:00:00, Avg Next Day Returns: -2.39447993277

##### Testing events aggregately: 

In [9]:
# Create a dictionary to store the result for threshold 3std
results_dict_b_three_increase_alt_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 8% threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_3std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_three_increase_alt_m['Company'].append(i)
        results_dict_b_three_increase_alt_m['Event_Date'].append(event_date)
        results_dict_b_three_increase_alt_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_increase_alt_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_increase_alt_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_increase_alt_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_three_increase_alt_m = pd.DataFrame(results_dict_b_three_increase_alt_m)

results_significance_b_three_increase_alt_result_m = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_three_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m['Avg_Next_Day_Returns'].mean())
results_significance_b_three_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m['Avg_Next_2_Days_Returns'].mean())
results_significance_b_three_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m['Avg_Next_5_Days_Returns'].mean())
results_significance_b_three_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m['p_value'].append(result_20)
results_significance_b_three_increase_alt_result_m=pd.DataFrame(results_significance_b_three_increase_alt_result_m)

# Create a dictionary to store the result for threshold 4std

results_dict_b_four_increase_alt_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 10% threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_4std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_four_increase_alt_m['Company'].append(i)
        results_dict_b_four_increase_alt_m['Event_Date'].append(event_date)
        results_dict_b_four_increase_alt_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_increase_alt_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_increase_alt_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_increase_alt_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_four_increase_alt_m = pd.DataFrame(results_dict_b_four_increase_alt_m)

results_significance_b_four_increase_alt_result_m = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_four_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m['Avg_Next_Day_Returns'].mean())
results_significance_b_four_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m['Avg_Next_2_Days_Returns'].mean())
results_significance_b_four_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m['Avg_Next_5_Days_Returns'].mean())
results_significance_b_four_increase_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m['p_value'].append(result_20)
results_significance_b_four_increase_alt_result_m=pd.DataFrame(results_significance_b_four_increase_alt_result_m)

print(results_significance_b_three_increase_alt_result_m.head())
print(results_significance_b_four_increase_alt_result_m.head())


Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next Day Returns: 8.107344089646741
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 2 Days Returns: -1.97577369993215 
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 5 Days Returns: 0.7669898161524522
Company: ACAD.ST, Date: 2017-09-20 00:00:00, Avg Next 20 Days Returns: 0.2875533134243679
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next Day Returns: 8.107344089646741
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 2 Days Returns: -3.3488321812843873 
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 5 Days Returns: -1.7053771556136645
Company: ACAD.ST, Date: 2018-09-12 00:00:00, Avg Next 20 Days Returns: -0.012487821302648517
Company: ACAD.ST, Date: 2019-01-16 00:00:00, Avg Next Day Returns: 8.107344089646741
Company: ACAD.ST, Date: 2019-01-16 00:00:00, Avg Next 2 Days Returns: -2.709448786503146 
Company: ACAD.ST, Date: 2019-01-16 00:00:00, Avg Next 5 Days Returns: -0.1803944030900234
Company: ACAD.ST, Date:

#### Price increases with market decreases: 

##### Testing events individually: 

In [10]:

# Create a dictionary to store the result for each threshold
results_dict_b_three_increase_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

results_dict_b_four_increase_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_3std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue


        results_dict_b_three_increase_m_dec['Company'].append(i)
        results_dict_b_three_increase_m_dec['Event_Date'].append(event_date)
        results_dict_b_three_increase_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_increase_m_dec['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_three_increase_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_increase_m_dec['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_three_increase_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_increase_m_dec['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_three_increase_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_three_increase_m_dec['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_three_increase_m_dec = pd.DataFrame(results_dict_b_three_increase_m_dec)


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_4std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue

        results_dict_b_four_increase_m_dec['Company'].append(i)
        results_dict_b_four_increase_m_dec['Event_Date'].append(event_date)
        results_dict_b_four_increase_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_increase_m_dec['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_four_increase_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_increase_m_dec['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_four_increase_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_increase_m_dec['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_four_increase_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_four_increase_m_dec['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_four_increase_m_dec = pd.DataFrame(results_dict_b_four_increase_m_dec)
print(results_significance_b_three_increase_m_dec.head())
print(results_significance_b_four_increase_m_dec.head())


Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next Day Returns: -5.173443823384285 , P value: nan 
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 2 Days Returns: -3.8307428583604795,P value: 0.2146211628395721 
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 5 Days Returns: -0.22193830294331232,P value: 0.9461787052990721 
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 20 Days Returns: 1.3306085285930964,P value: 0.20268550751904987 
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next Day Returns: 7.460290117221901 , P value: nan 
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 2 Days Returns: 3.142098705092493,P value: 0.5995419967453051 
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 5 Days Returns: 0.706795316217113,P value: 0.7191280202390646 
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 20 Days Returns: -0.1977987118726808,P value: 0.8400891031479124 
Company: ACAD.ST, Date: 2021-09-29 00:00:00, Avg Next Day Returns: -8.07776473151657

##### Testing events aggregately: 

In [11]:
# Create a dictionary to store the result for threshold 3std
results_dict_b_three_increase_alt_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_3std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_three_increase_alt_m_dec['Company'].append(i)
        results_dict_b_three_increase_alt_m_dec['Event_Date'].append(event_date)
        results_dict_b_three_increase_alt_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_increase_alt_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_increase_alt_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_increase_alt_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_three_increase_alt_m_dec = pd.DataFrame(results_dict_b_three_increase_alt_m_dec)

results_significance_b_three_increase_alt_result_m_dec = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_three_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m_dec['Avg_Next_Day_Returns'].mean())
results_significance_b_three_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m_dec['Avg_Next_2_Days_Returns'].mean())
results_significance_b_three_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m_dec['Avg_Next_5_Days_Returns'].mean())
results_significance_b_three_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_increase_alt_m_dec['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m_dec['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m_dec['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m_dec['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_increase_alt_result_m_dec['p_value'].append(result_20)
results_significance_b_three_increase_alt_result_m_dec=pd.DataFrame(results_significance_b_three_increase_alt_result_m_dec)

# Create a dictionary to store the result for threshold 4std

results_dict_b_four_increase_alt_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Increase_4std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_four_increase_alt_m_dec['Company'].append(i)
        results_dict_b_four_increase_alt_m_dec['Event_Date'].append(event_date)
        results_dict_b_four_increase_alt_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_increase_alt_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_increase_alt_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_increase_alt_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_four_increase_alt_m_dec = pd.DataFrame(results_dict_b_four_increase_alt_m_dec)

results_significance_b_four_increase_alt_result_m_dec = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_four_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m_dec['Avg_Next_Day_Returns'].mean())
results_significance_b_four_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m_dec['Avg_Next_2_Days_Returns'].mean())
results_significance_b_four_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m_dec['Avg_Next_5_Days_Returns'].mean())
results_significance_b_four_increase_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_increase_alt_m_dec['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m_dec['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m_dec['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m_dec['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_increase_alt_result_m_dec['p_value'].append(result_20)
results_significance_b_four_increase_alt_result_m_dec=pd.DataFrame(results_significance_b_four_increase_alt_result_m_dec)

print(results_significance_b_three_increase_alt_result_m_dec.head())
print(results_significance_b_four_increase_alt_result_m_dec.head())


Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next Day Returns: -5.5810839903863085
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 2 Days Returns: -3.8307428583604795 
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 5 Days Returns: -0.22193830294331232
Company: ACAD.ST, Date: 2019-01-11 00:00:00, Avg Next 20 Days Returns: 1.3306085285930964
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next Day Returns: -5.5810839903863085
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 2 Days Returns: 3.142098705092493 
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 5 Days Returns: 0.706795316217113
Company: ACAD.ST, Date: 2020-01-31 00:00:00, Avg Next 20 Days Returns: -0.1977987118726808
Company: ACAD.ST, Date: 2021-09-29 00:00:00, Avg Next Day Returns: -5.5810839903863085
Company: ACAD.ST, Date: 2021-09-29 00:00:00, Avg Next 2 Days Returns: -2.2444305329711716 
Company: ACAD.ST, Date: 2021-09-29 00:00:00, Avg Next 5 Days Returns: -1.3911218635054652
Company: ACAD.ST, 

#### Price decreases with market increases: 

##### Testing events individually: 

In [12]:

# Create a dictionary to store the result for each threshold
results_dict_b_three_decrease_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

results_dict_b_four_decrease_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_3std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue


        results_dict_b_three_decrease_m['Company'].append(i)
        results_dict_b_three_decrease_m['Event_Date'].append(event_date)
        results_dict_b_three_decrease_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_decrease_m['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_three_decrease_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_decrease_m['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_three_decrease_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_decrease_m['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_three_decrease_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_three_decrease_m['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_three_decrease_m = pd.DataFrame(results_dict_b_three_decrease_m)


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_4std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue

        results_dict_b_four_decrease_m['Company'].append(i)
        results_dict_b_four_decrease_m['Event_Date'].append(event_date)
        results_dict_b_four_decrease_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_decrease_m['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_four_decrease_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_decrease_m['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_four_decrease_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_decrease_m['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_four_decrease_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_four_decrease_m['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_four_decrease_m = pd.DataFrame(results_dict_b_four_decrease_m)
print(results_significance_b_three_decrease_m.head())
print(results_significance_b_four_decrease_m.head())


Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next Day Returns: -0.59186748898083 , P value: nan 
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 2 Days Returns: -2.7808703616408494,P value: 0.4245396782037873 
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 5 Days Returns: -0.3979962427625766,P value: 0.852540886095299 
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 20 Days Returns: 0.5582087650053407,P value: 0.5605988475777701 
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next Day Returns: 0.5814374570472839 , P value: nan 
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 2 Days Returns: 0.7152220976753485,P value: 0.11772141643381721 
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 5 Days Returns: 0.9977870074600826,P value: 0.4645438346389374 
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 20 Days Returns: 0.9380843316819764,P value: 0.4386193634080757 
Company: ACAD.ST, Date: 2019-08-29 00:00:00, Avg Next Day Returns: 4.302667497555826 

##### Testing events aggregately: 

In [13]:
# Create a dictionary to store the result for threshold 8%
results_dict_b_three_decrease_alt_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_3std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_three_decrease_alt_m['Company'].append(i)
        results_dict_b_three_decrease_alt_m['Event_Date'].append(event_date)
        results_dict_b_three_decrease_alt_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_decrease_alt_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_decrease_alt_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_decrease_alt_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_three_decrease_alt_m = pd.DataFrame(results_dict_b_three_decrease_alt_m)

results_significance_b_three_decrease_alt_result_m = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_three_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m['Avg_Next_Day_Returns'].mean())
results_significance_b_three_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m['Avg_Next_2_Days_Returns'].mean())
results_significance_b_three_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m['Avg_Next_5_Days_Returns'].mean())
results_significance_b_three_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m['p_value'].append(result_20)
results_significance_b_three_decrease_alt_result_m=pd.DataFrame(results_significance_b_three_decrease_alt_result_m)

# Create a dictionary to store the result for threshold 4std

results_dict_b_four_decrease_alt_m = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_4std'] == 1) & (total_b_df['Market_Return_Increase'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_four_decrease_alt_m['Company'].append(i)
        results_dict_b_four_decrease_alt_m['Event_Date'].append(event_date)
        results_dict_b_four_decrease_alt_m['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_decrease_alt_m['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_decrease_alt_m['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_decrease_alt_m['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_four_decrease_alt_m = pd.DataFrame(results_dict_b_four_decrease_alt_m)

results_significance_b_four_decrease_alt_result_m = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_four_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m['Avg_Next_Day_Returns'].mean())
results_significance_b_four_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m['Avg_Next_2_Days_Returns'].mean())
results_significance_b_four_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m['Avg_Next_5_Days_Returns'].mean())
results_significance_b_four_decrease_alt_result_m['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m['p_value'].append(result_20)
results_significance_b_four_decrease_alt_result_m=pd.DataFrame(results_significance_b_four_decrease_alt_result_m)

print(results_significance_b_three_decrease_alt_result_m.head())
print(results_significance_b_four_decrease_alt_result_m.head())


Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next Day Returns: -0.9787823282366566
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 2 Days Returns: -2.7808703616408494 
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 5 Days Returns: -0.3979962427625766
Company: ACAD.ST, Date: 2018-06-29 00:00:00, Avg Next 20 Days Returns: 0.5582087650053407
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next Day Returns: -0.9787823282366566
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 2 Days Returns: 0.7152220976753485 
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 5 Days Returns: 0.9977870074600826
Company: ACAD.ST, Date: 2018-08-29 00:00:00, Avg Next 20 Days Returns: 0.9380843316819764
Company: ACAD.ST, Date: 2019-08-29 00:00:00, Avg Next Day Returns: -0.9787823282366566
Company: ACAD.ST, Date: 2019-08-29 00:00:00, Avg Next 2 Days Returns: 1.5146605798916175 
Company: ACAD.ST, Date: 2019-08-29 00:00:00, Avg Next 5 Days Returns: 0.3335219484457421
Company: ACAD.ST, Da

#### Price decreases with market decreases: 

##### Testing events individually: 

In [14]:

# Create a dictionary to store the result for each threshold
results_dict_b_three_decrease_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

results_dict_b_four_decrease_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'P_Value_1_Day': [],
                'Avg_Next_2_Days_Returns': [],
                'P_Value_2_Days': [],
                'Avg_Next_5_Days_Returns': [],
                'P_Value_5_Days': [],
                'Avg_Next_20_Days_Returns': [],
                'P_Value_20_Days': []}

# Calculate average ARs and p-values for 8% threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_3std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue


        results_dict_b_three_decrease_m_dec['Company'].append(i)
        results_dict_b_three_decrease_m_dec['Event_Date'].append(event_date)
        results_dict_b_three_decrease_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_decrease_m_dec['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_three_decrease_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_decrease_m_dec['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_three_decrease_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_decrease_m_dec['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_three_decrease_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_three_decrease_m_dec['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_three_decrease_m_dec = pd.DataFrame(results_dict_b_three_decrease_m_dec)


# Calculate average ARs and p-values for 10% threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_4std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1
        idx_event_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0]

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

        # Average_next_day
            avg_next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            p_value_1_day = ttest_1samp(avg_next_day_returns,0, alternative='two-sided').pvalue


            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()
            p_value_2_days = ttest_1samp(next_2_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()
            p_value_5_days = ttest_1samp(next_5_days_returns, 0, alternative='two-sided').pvalue

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()
            p_value_20_days = ttest_1samp(next_20_days_returns, 0, alternative='two-sided').pvalue

        results_dict_b_four_decrease_m_dec['Company'].append(i)
        results_dict_b_four_decrease_m_dec['Event_Date'].append(event_date)
        results_dict_b_four_decrease_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_decrease_m_dec['P_Value_1_Day'].append(p_value_1_day)
        results_dict_b_four_decrease_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_decrease_m_dec['P_Value_2_Days'].append(p_value_2_days)
        results_dict_b_four_decrease_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_decrease_m_dec['P_Value_5_Days'].append(p_value_5_days)
        results_dict_b_four_decrease_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)
        results_dict_b_four_decrease_m_dec['P_Value_20_Days'].append(p_value_20_days)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns} , P value: {p_value_1_day} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns},P value: {p_value_2_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns},P value: {p_value_5_days} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns},P value: {p_value_20_days} ')

results_significance_b_four_decrease_m_dec = pd.DataFrame(results_dict_b_four_decrease_m_dec)
print(results_significance_b_three_decrease_m_dec.head())
print(results_significance_b_four_decrease_m_dec.head())


Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next Day Returns: 0.49472219529248096 , P value: nan 
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 2 Days Returns: -0.32729385328417904,P value: 0.7587726056051532 
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 5 Days Returns: -0.8076192808147639,P value: 0.45079604574904786 
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 20 Days Returns: 0.3821379219220112,P value: 0.5960015925012139 
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next Day Returns: 9.274323356457607 , P value: nan 
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 2 Days Returns: 1.8432717699513743,P value: 0.8452107052758301 
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 5 Days Returns: -1.6803886751619719,P value: 0.5882843501970578 
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 20 Days Returns: 0.9851440456825676,P value: 0.5913175942785516 
Company: ACAD.ST, Date: 2020-03-12 00:00:00, Avg Next Day Returns: -6.69914099476

##### Testing events aggregately: 

In [15]:
# Create a dictionary to store the result for threshold 3std
results_dict_b_three_decrease_alt_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 3std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_3std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_three_decrease_alt_m_dec['Company'].append(i)
        results_dict_b_three_decrease_alt_m_dec['Event_Date'].append(event_date)
        results_dict_b_three_decrease_alt_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_three_decrease_alt_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_three_decrease_alt_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_three_decrease_alt_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_three_decrease_alt_m_dec = pd.DataFrame(results_dict_b_three_decrease_alt_m_dec)

results_significance_b_three_decrease_alt_result_m_dec = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_three_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m_dec['Avg_Next_Day_Returns'].mean())
results_significance_b_three_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m_dec['Avg_Next_2_Days_Returns'].mean())
results_significance_b_three_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m_dec['Avg_Next_5_Days_Returns'].mean())
results_significance_b_three_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_three_decrease_alt_m_dec['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m_dec['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m_dec['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m_dec['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_three_decrease_alt_result_m_dec['p_value'].append(result_20)
results_significance_b_three_decrease_alt_result_m_dec=pd.DataFrame(results_significance_b_three_decrease_alt_result_m_dec)

# Create a dictionary to store the result for threshold 10%

results_dict_b_four_decrease_alt_m_dec = {'Company': [],
                'Event_Date': [],
                'Avg_Next_Day_Returns': [],
                'Avg_Next_2_Days_Returns': [],
                'Avg_Next_5_Days_Returns': [],
                'Avg_Next_20_Days_Returns': []}
Next_Day_Returns=[]
Next_2_Days_Returns=[]
Next_5_Days_Returns=[]
Next_20_Days_Returns=[]


# Calculate average ARs and p-values for 4std threshold
for i in df_mid['Security-Symbol']:

    rows_with_condition = total_b_df[(total_b_df[f'{i}_Decrease_4std'] == 1) & (total_b_df['Market_Return_Decrease'] == 1)]

    for index, row in rows_with_condition.iterrows():

        # Date with large price change
        event_date = row['Date']

        # Index_next_day
        idx_next_day = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1

        # Index_next_2_days
        idx_next_2_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2
        next_2_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 2, f'{i}_ARs']
        list_2=next_2_days_returns.dropna().to_list()
        Next_2_Days_Returns.extend(list_2)

        # Index_next_5_days
        idx_next_5_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5
        next_5_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 5, f'{i}_ARs']
        list_5=next_5_days_returns.dropna().to_list()
        Next_5_Days_Returns.extend(list_5)

        # Index_next_20_days
        idx_next_20_days = total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20
        next_20_days_returns = total_b_df.loc[total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 1: total_b_df.index[total_b_df['Date'] == event_date].to_numpy()[0] + 20, f'{i}_ARs']
        list_20=next_20_days_returns.dropna().to_list()
        Next_20_Days_Returns.extend(list_20)


        if idx_next_day < len(total_b_df) and idx_next_2_days < len(total_b_df) and \
           idx_next_5_days < len(total_b_df) and idx_next_20_days < len(total_b_df):

            # Average_next_day
            next_day_returns = total_b_df.at[idx_next_day, f'{i}_ARs']
            Next_Day_Returns.append(next_day_returns)

            # Average_next_2_days
            avg_next_2_days_returns = next_2_days_returns.mean()

            # Average_next_5_days
            avg_next_5_days_returns = next_5_days_returns.mean()

            # Average_next_20_days
            avg_next_20_days_returns = next_20_days_returns.mean()


        results_dict_b_four_decrease_alt_m_dec['Company'].append(i)
        results_dict_b_four_decrease_alt_m_dec['Event_Date'].append(event_date)
        results_dict_b_four_decrease_alt_m_dec['Avg_Next_Day_Returns'].append(avg_next_day_returns)
        results_dict_b_four_decrease_alt_m_dec['Avg_Next_2_Days_Returns'].append(avg_next_2_days_returns)
        results_dict_b_four_decrease_alt_m_dec['Avg_Next_5_Days_Returns'].append(avg_next_5_days_returns)
        results_dict_b_four_decrease_alt_m_dec['Avg_Next_20_Days_Returns'].append(avg_next_20_days_returns)



        print(f'Company: {i}, Date: {event_date}, Avg Next Day Returns: {avg_next_day_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 2 Days Returns: {avg_next_2_days_returns} ')
        print(f'Company: {i}, Date: {event_date}, Avg Next 5 Days Returns: {avg_next_5_days_returns}')
        print(f'Company: {i}, Date: {event_date}, Avg Next 20 Days Returns: {avg_next_20_days_returns}')

results_significance_b_four_decrease_alt_m_dec = pd.DataFrame(results_dict_b_four_decrease_alt_m_dec)

results_significance_b_four_decrease_alt_result_m_dec = {'Window':['1','1-2','1-5','1-20'],
                                                    'Avg_ARs_%':[],
                                                    'p_value':[]}
results_significance_b_four_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m_dec['Avg_Next_Day_Returns'].mean())
results_significance_b_four_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m_dec['Avg_Next_2_Days_Returns'].mean())
results_significance_b_four_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m_dec['Avg_Next_5_Days_Returns'].mean())
results_significance_b_four_decrease_alt_result_m_dec['Avg_ARs_%'].append(results_significance_b_four_decrease_alt_m_dec['Avg_Next_20_Days_Returns'].mean())

result_1=ttest_1samp(Next_Day_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m_dec['p_value'].append(result_1)

result_2=ttest_1samp(Next_2_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m_dec['p_value'].append(result_2)
result_5=ttest_1samp(Next_5_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m_dec['p_value'].append(result_5)
result_20=ttest_1samp(Next_20_Days_Returns,popmean=0,alternative='two-sided').pvalue
results_significance_b_four_decrease_alt_result_m_dec['p_value'].append(result_20)
results_significance_b_four_decrease_alt_result_m_dec=pd.DataFrame(results_significance_b_four_decrease_alt_result_m_dec)

print(results_significance_b_three_decrease_alt_result_m_dec.head())
print(results_significance_b_four_decrease_alt_result_m_dec.head())


Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next Day Returns: -12.863918527645055
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 2 Days Returns: -0.32729385328417904 
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 5 Days Returns: -0.8076192808147639
Company: ACAD.ST, Date: 2019-05-07 00:00:00, Avg Next 20 Days Returns: 0.3821379219220112
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next Day Returns: -12.863918527645055
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 2 Days Returns: 1.8432717699513743 
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 5 Days Returns: -1.6803886751619719
Company: ACAD.ST, Date: 2020-03-09 00:00:00, Avg Next 20 Days Returns: 0.9851440456825676
Company: ACAD.ST, Date: 2020-03-12 00:00:00, Avg Next Day Returns: -12.863918527645055
Company: ACAD.ST, Date: 2020-03-12 00:00:00, Avg Next 2 Days Returns: -5.04436210958691 
Company: ACAD.ST, Date: 2020-03-12 00:00:00, Avg Next 5 Days Returns: -0.44877507085113033
Company: ACAD.ST,

In [16]:
results_significance_b_three_increase_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_increase_m_mid.xlsx')
results_significance_b_four_increase_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_increase_m_mid.xlsx')

results_significance_b_three_increase_alt_result_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_increase_alt_result_m_mid.xlsx')
results_significance_b_four_increase_alt_result_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_increase_alt_result_m_mid.xlsx')

results_significance_b_three_increase_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_increase_m_dec_mid.xlsx')
results_significance_b_four_increase_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_increase_m_dec_mid.xlsx')

results_significance_b_three_increase_alt_result_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_increase_alt_result_m_dec_mid.xlsx')
results_significance_b_four_increase_alt_result_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_increase_alt_result_m_dec_mid.xlsx')

results_significance_b_three_decrease_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_decrease_m_mid.xlsx')
results_significance_b_four_decrease_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_decrease_m_mid.xlsx')

results_significance_b_three_decrease_alt_result_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_decrease_alt_result_m_mid.xlsx')
results_significance_b_four_decrease_alt_result_m.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_decrease_alt_result_m_mid.xlsx')

results_significance_b_three_decrease_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_decrease_m_dec_mid.xlsx')
results_significance_b_four_decrease_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_decrease_m_dec_mid.xlsx')

results_significance_b_three_decrease_alt_result_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_three_decrease_alt_result_m_dec_mid.xlsx')
results_significance_b_four_decrease_alt_result_m_dec.to_excel(f'{path}/raw_data/main/t3_results_significance_b_four_decrease_alt_result_m_dec_mid.xlsx')
